In [1]:
# import packages
import pandas as pd
import altair as alt

In [2]:
# load data
gdp_df = pd.read_csv("ds4200_project_co2_data.csv")
gdp_df

Unnamed: 0  index      country  year iso_code  population           gdp  \
0              0    140  Afghanistan  1990      AFG  10694804.0  1.306598e+10   
1              1    141  Afghanistan  1991      AFG  10745168.0  1.204736e+10   
2              2    142  Afghanistan  1992      AFG  12057436.0  1.267754e+10   
3              3    143  Afghanistan  1993      AFG  14003764.0  9.834582e+09   
4              4    144  Afghanistan  1994      AFG  15455560.0  7.919857e+09   
...          ...    ...          ...   ...      ...         ...           ...   
8444        8444  47410     Zimbabwe  2018      ZWE  15052191.0  2.678627e+10   
8445        8445  47411     Zimbabwe  2019      ZWE  15354606.0  2.514642e+10   
8446        8446  47412     Zimbabwe  2020      ZWE  15669663.0  2.317871e+10   
8447        8447  47413     Zimbabwe  2021      ZWE  15993525.0  2.514009e+10   
8448        8448  47414     Zimbabwe  2022      ZWE  16320539.0  2.590159e+10   

         co2  co2_including_luc  co2_growth_prct  ...  co2_per_gdp  \
0      2.024              2.213          -26.784  ...        0.155   
1      1.914              1.938           -5.435  ...        0.159   
2      1.482             -0.158          -22.580  ...        0.117   
3      1.487             -2.557            0.330  ...        0.151   
4      1.454             -2.162           -2.227  ...        0.184   
...      ...                ...              ...  ...          ...   
8444  10.715             19.423           15.265  ...        0.400   
8445   9.775             17.854           -8.765  ...        0.389   
8446   7.850             15.459          -19.700  ...        0.339   
8447   8.396             15.513            6.962  ...        0.334   
8448   8.856             15.580            5.477  ...        0.342   

      co2_per_unit_energy  cement_co2  coal_co2  flaring_co2  gas_co2  \
0                   0.064       0.046     0.278        0.026    0.403   
1                   0.138       0.046     0.250        0.026    0.389   
2                   0.162       0.046     0.022        0.022    0.363   
3                   0.163       0.047     0.018        0.022    0.352   
4                   0.165       0.047     0.015        0.022    0.338   
...                   ...         ...       ...          ...      ...   
8444                0.207       0.558     6.097        0.000    0.000   
8445                0.212       0.473     5.571        0.000    0.000   
8446                0.187       0.496     4.309        0.000    0.000   
8447                0.199       0.531     4.548        0.000    0.000   
8448                  NaN       0.531     5.027        0.000    0.000   

      land_use_change_co2  oil_co2  trade_co2  other_industry_co2  
0                   0.189    1.271        NaN                 NaN  
1                   0.023    1.204        NaN                 NaN  
2                  -1.640    1.030        NaN                 NaN  
3                  -4.044    1.048        NaN                 NaN  
4                  -3.616    1.032        NaN                 NaN  
...                   ...      ...        ...                 ...  
8444                8.708    4.060     -0.088                 NaN  
8445                8.079    3.731      0.143                 NaN  
8446                7.609    3.045      0.818                 NaN  
8447                7.117    3.317      1.088                 NaN  
8448                6.724    3.298        NaN                 NaN  

[8449 rows x 21 columns]

In [3]:
# filtering for emmision types
co2_sources = ['co2', 'coal_co2', 'gas_co2', 'oil_co2', 'cement_co2', 'flaring_co2', 'land_use_change_co2', 'trade_co2', 'other_industry_co2']
gdp_df_melt = gdp_df.melt(id_vars=['country', 'year', 'gdp'], value_vars=co2_sources, var_name='co2_source', value_name='emissions')
gdp_df_melt

country  year           gdp          co2_source  emissions
0      Afghanistan  1990  1.306598e+10                 co2      2.024
1      Afghanistan  1991  1.204736e+10                 co2      1.914
2      Afghanistan  1992  1.267754e+10                 co2      1.482
3      Afghanistan  1993  9.834582e+09                 co2      1.487
4      Afghanistan  1994  7.919857e+09                 co2      1.454
...            ...   ...           ...                 ...        ...
76036     Zimbabwe  2018  2.678627e+10  other_industry_co2        NaN
76037     Zimbabwe  2019  2.514642e+10  other_industry_co2        NaN
76038     Zimbabwe  2020  2.317871e+10  other_industry_co2        NaN
76039     Zimbabwe  2021  2.514009e+10  other_industry_co2        NaN
76040     Zimbabwe  2022  2.590159e+10  other_industry_co2        NaN

[76041 rows x 5 columns]

In [15]:
gdp_df_melt = gdp_df_melt.loc[gdp_df_melt['country'] != 'World']

In [21]:
# creating interactive filters
alt.data_transformers.disable_max_rows()
# dropdown menu for different source types
industry_dropdown = alt.binding_select(options=co2_sources, name='CO2 Source')
industry_selection = alt.selection_single(fields=['co2_source'], bind=industry_dropdown)

# slider for years
year_slider = alt.binding_range(min = gdp_df_melt['year'].min(), max = gdp_df_melt['year'].max(), step = 1, name = "Year")
year_selection = alt.selection_point(fields=['year'], bind = year_slider)

scatter = alt.Chart(gdp_df_melt).mark_circle(size = 60, opacity = 0.5).encode(
    alt.X('gdp:Q',
          axis=alt.Axis(title='GDP (USD)')),
    alt.Y('emissions:Q',
          axis=alt.Axis(title='CO2 Emissions (Million Tonnes)')),
    alt.Color('country:N', legend=None),
    tooltip=[
        alt.Tooltip('country:N', title='Country'),
        alt.Tooltip('gdp:Q', title='GDP (USD)'),
        alt.Tooltip('emissions:Q', title='CO2 Emissions (Million Tonnes)'),
        alt.Tooltip('year:Q', title='Year')
    ]
).add_params(
    industry_selection,
    year_selection
).transform_filter(
    industry_selection
).transform_filter(
    year_selection
).interactive()

scatter

/Users/alextu/anaconda3/envs/ds3500/lib/python3.12/site-packages/altair/utils/deprecation.py:65: AltairDeprecationWarning: 'selection_single' is deprecated.  Use 'selection_point'
  warnings.warn(message, AltairDeprecationWarning, stacklevel=1)
/Users/alextu/anaconda3/envs/ds3500/lib/python3.12/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Users/alextu/anaconda3/envs/ds3500/lib/python3.12/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)


alt.Chart(...)

In [22]:
scatter.save('gdp_co2_scatter.html')

/Users/alextu/anaconda3/envs/ds3500/lib/python3.12/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Users/alextu/anaconda3/envs/ds3500/lib/python3.12/site-packages/altair/utils/core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
